In [ ]:
# Temizleme işlemini gerçekleştirin
import re
import pandas as pd
import nltk
from nltk.corpus import stopwords

# NLTK stopwords'ü indir
nltk.download('stopwords')
# Stopwords dosyasını okuma ve liste haline getirme

def load_stop_words(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        stop_words = {line.strip().lower() for line in file}
    return stop_words

# Örneğin 'stopwords.txt' dosyasını kullanarak stopwords'leri yükleyin
custom_stop_words = load_stop_words('gereksiz_kelimeler.txt')



# CSV dosyasını yükleme

df= pd.read_csv('texts_egitim.csv')
# 'metinler' sütununu çekme
metinler= df['metinler'].tolist()[:10000]

# Metin temizleme fonksiyonu
def clean_text(text,custom_stop_words):
    # Metni küçük harfe çevirme
    text = text.lower()
    # Noktalama işaretlerini ve sayıları temizleme
    text = re.sub(r'\d+', '', text)  # Sayıları çıkar
    text = re.sub(r'[^\w\s]', '', text)  # Noktalama işaretlerini çıkar
    
    # Gereksiz kelimeleri çıkarma
    words = text.split()
    filtered_words = [word for word in words if word not in custom_stop_words]
    # Çıkarılan kelimeleri sözlüğe ekleyelim
    # Çıkarılan kelimeleri kümeye ekleyelim
    
    removed=set()
    for word in words:
        if word not in filtered_words:
            removed.add(word)
    cleaned_text = ' '.join(filtered_words)
    # If no words remain after cleaning, return an empty string
    if not cleaned_text:
        return ''
    return cleaned_text
# Metinleri temizleme işlemi ve çıkarılan kelimeleri toplama
all_removed_words = set()
df['temizlenmis_metin'] = df['metinler'].apply(lambda x: clean_text(x, custom_stop_words)[0])
df['removed_words'] = df['metinler'].apply(lambda x: clean_text(x, custom_stop_words)[1])
all_removed_words.update(*df['removed_words'])

# Tüm çıkarılan kelimeleri ekrana yazdırma veya dosyaya kaydetme
print("Tüm Çıkarılan Kelimeler:")
for word in all_removed_words:
    print(word)
    
# Çıkarılan kelimeleri bir dosyaya kaydetmek için:
with open('cikarilan_kelimeler.csv', 'w') as f:
    for word in all_removed_words:
        f.write(word + '\n')

# Filtrelenmiş kelimelerden yeni bir metin listesi oluşturma
yeni_metin_listesi = []
for metin in metinler:
    kelimeler = metin.split()
    # Burada gereksiz kelime listesinden kelimeler çıkarılma işlemi yapılırsa daha iyi olur
    # Örneğin:
    # kelimeler = [kelime for kelime in kelimeler if kelime not in gereksiz_kelime_listesi]
    yeni_metin_listesi.append(' '.join(kelimeler))

# Yeni metin listesini kaydetme (örneğin bir dosyaya)
with open('yeni_metinler.txt', 'w', encoding='utf-8') as f:
    for metin in yeni_metin_listesi:
        f.write(metin + '\n')




# Metinleri temizleme işlemi
df['temizlenmis_metin'] = df['metinler'].apply(lambda x: clean_text(x, custom_stop_words))

print(df[['metinler', 'temizlenmis_metin']])
# Yeni bir DataFrame oluşturarak temizlenmiş metinleri atayın
df_temiz = pd.DataFrame({'temizlenmis_metin': df['temizlenmis_metin']})

# CSV dosyasına kaydetme
df_temiz.to_csv('temizlenmis_metin2.csv', index=False)


In [14]:
import re
import pandas as pd
import nltk
from nltk.corpus import stopwords

# NLTK stopwords'ü indir
nltk.download('stopwords')

# Stopwords dosyasını okuma ve liste haline getirme
def load_stop_words(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        stop_words = {line.strip().lower() for line in file}
    return stop_words

# Örneğin 'stopwords.txt' dosyasını kullanarak stopwords'leri yükleyin
custom_stop_words = load_stop_words('gereksiz_kelimeler.txt')

# CSV dosyasını yükleme
df = pd.read_csv('texts_egitim.csv')

# 'metinler' sütununu çekme
metinler = df['metinler'].tolist()[:10000]

# Metin temizleme fonksiyonu
def clean_text(text, custom_stop_words):
    # Metni küçük harfe çevirme
    text = text.lower()
    # Noktalama işaretlerini ve sayıları temizleme
    text = re.sub(r'\d+', '', text)  # Sayıları çıkar
    text = re.sub(r'[^\w\s]', '', text)  # Noktalama işaretlerini çıkar
    
    # Gereksiz kelimeleri çıkarma
    words = text.split()
    filtered_words = [word for word in words if word not in custom_stop_words]
    
    # Çıkarılan kelimeleri belirleme
    removed = set(words) - set(filtered_words)
    
    cleaned_text = ' '.join(filtered_words)
    
    # Eğer temizlenmiş metin boşsa, boş string döndür
    if not cleaned_text:
        return '', removed
    
    return cleaned_text, removed

# Metinleri temizleme işlemi ve çıkarılan kelimeleri toplama
df[['temizlenmis_metin', 'removed_words']] = df.apply(lambda row: pd.Series(clean_text(row['metinler'], custom_stop_words)), axis=1)

# Tüm çıkarılan kelimeleri toplama
all_removed_words = set()
for removed in df['removed_words']:
    all_removed_words.update(removed)

# Tüm çıkarılan kelimeleri ekrana yazdırma veya dosyaya kaydetme
print("Tüm Çıkarılan Kelimeler:")
for word in all_removed_words:
    print(word)
    
# Çıkarılan kelimeleri bir dosyaya kaydetmek için:
with open('cikarilan_kelimeler.csv', 'w', encoding='utf-8') as f:
    for word in all_removed_words:
        f.write(word + '\n')

# Yeni metin listesini oluşturma ve dosyaya yazma
with open('yeni_metinler.txt', 'w', encoding='utf-8') as f:
    for metin in df['temizlenmis_metin']:
        f.write(metin + '\n')

# Temizlenmiş metinleri CSV dosyasına kaydetme
df_temiz = df[['temizlenmis_metin']]
df_temiz.to_csv('temizlenmis_metin2.csv', index=False)


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\info\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Tüm Çıkarılan Kelimeler:
baktı
epeyce
alt
merhamet
çiçeği
olunan
elime
konuşup
döneme
içki
belirlediği
tarımsal
nba
moda
olaya
kraliyet
kime
bakıldığında
takımda
yla
aya
öte
sırrı
uzattı
zorunlu
onunla
yükseliyordu
uygulanması
çalıştığını
takım
kampanyası
ndaki
aileye
yönetici
iddianamede
suçlu
önerdi
saati
kürtçe
askıya
elden
mülteci
evrim
cevap
geçmesini
haftada
beynin
potansiyel
boşuna
kaptanı
göndermek
rehber
emin
karşılaşmanın
hem
maça
yapılmıştır
görünce
yetersiz
yalan
konularda
filmleri
kapattı
marka
kurulmuştur
hızla
lisans
istiyorsun
sonuçta
ürkütücü
etnik
önünden
yukarıda
öz
hizmetçi
alarak
uyarınca
nasip
ulaştığını
bulanık
kurucusu
çıkarmak
arabanın
ülkenin
first
damla
vermektedir
görmüş
tabiat
verdiğini
umutsuz
man
oda
verilir
daniel
taş
sırf
hükümet
sanıklar
olurlar
kadro
tel
tesadüf
görmedi
açıklanan
mektuplar
çalışıyoruz
maliki
vallahi
amacına
galatasaray
ayın
taraftarlar
istediği
bakışta
mart
tarihli
nesne
otelin
arayarak
uzaklaştı
görülmüştür
ismet
mike
kişiyi
sevilen


TF-Idf ile metinlerdeki anahtar kelimeleri 10'ar keyworde indirdik ve skorlarını aldık 

In [9]:
import pandas as pd
import csv
from sklearn.feature_extraction.text import TfidfVectorizer
from joblib import Parallel, delayed
from tqdm import tqdm


def extract_keywords_tfidf(metinler, stop_words_list, top_n=10, n_jobs=-1):
    """TF-IDF ile anahtar kelimeleri çıkarır, stop words listesi ile birlikte kullanır ve paralel işlem yapar."""
    vectorizer = TfidfVectorizer(stop_words=stop_words_list)



    # TF-IDF matrisini oluşturma (CPU kullanımını optimize etmek için n_jobs kullanılır)
    X = vectorizer.fit_transform(metinler)  # bunu csv'den okudum
    feature_names = vectorizer.get_feature_names_out()  # Her kelimenin tf-idf vektöründeki karşılığını tutar

    # tf-idf değerlerini paralel işlemeyle bulma
    def process_row(row):
        tfidf_scores = row.toarray().flatten()  # Düz bir değişken haline getirme
        top_indices = tfidf_scores.argsort()[-top_n:][::-1]  # En yüksek n skoru bul

        # En yüksek skorlu kelimeleri ve skorları bul
        top_keywords = [feature_names[i] for i in top_indices]
        top_tfidf_scores = [tfidf_scores[i] for i in top_indices]
        return top_keywords, top_tfidf_scores

    results = Parallel(n_jobs=n_jobs)(delayed(process_row)(row) for row in tqdm(X))

    # Sonuçları listelere ayırma
    top_keywords_per_document, top_tfidf_scores_per_document = zip(*results)

    return top_keywords_per_document, top_tfidf_scores_per_document



df = pd.read_csv("temizlenmis_metin.csv", encoding='utf-8', on_bad_lines='skip')
metinler = df["temizlenmis_metin"].fillna("").tolist()


with open("gereksiz_kelimeler.txt", "r", encoding='utf-8') as f:
    stop_words_list = f.read().splitlines()
    

combined_sample = metinler[:10000]
top_keywords_per_document, top_tfidf_scores_per_document = extract_keywords_tfidf(combined_sample, stop_words_list, top_n=10, n_jobs=-1)
#n__jobs ın 2 olması aynı anda iki iş parçacığı yani iki işlem yanı anda yürütülür
#n__jobs ın -1 olması maksimum işlemci sayısının kullanılmasıdır.


with open('keywords.csv', mode='w', newline='', encoding='utf-8') as file:
    writer = csv.writer(file)
    # Başlık satırını yazma
    writer.writerow(['Document_Index'] + [f'Keyword_{i+1}' for i in range(10)] + [f'Score_{i+1}' for i in range(10)])

    # Her döküman için anahtar kelimeler ve skorları yazma
    for i, (keywords, scores) in enumerate(zip(top_keywords_per_document, top_tfidf_scores_per_document)):
        row = [i+1] + keywords + [f"{score:.4f}" for score in scores]
        writer.writerow(row)

print("Sonuçlar 'keywords.csv' dosyasına kaydedildi.")
"""
# Sonuçları görüntüleme
for i, (keywords, scores) in enumerate(zip(top_keywords_per_document, top_tfidf_scores_per_document)):
    print(f"Döküman {i+1}:")
    for keyword, score in zip(keywords, scores):
        print(f"{keyword}: {score:.4f}")
    print("\n")
"""

c:\gitProjects\yeni\.venv\lib\site-packages\sklearn\feature_extraction\text.py:406: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['bağlantılar', 'leh'] not in stop_words.
  warnings.warn(
10000it [15:12, 10.96it/s]


Sonuçlar 'keywords.csv' dosyasına kaydedildi.


'\n# Sonuçları görüntüleme\nfor i, (keywords, scores) in enumerate(zip(top_keywords_per_document, top_tfidf_scores_per_document)):\n    print(f"Döküman {i+1}:")\n    for keyword, score in zip(keywords, scores):\n        print(f"{keyword}: {score:.4f}")\n    print("\n")\n'

In [23]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity


def clean_text(text):
    if pd.isna(text):
        return ''
    return text

# CSV dosyasından belirli sayıda metin okuma
def get_text(file_path='temizlenmis_metin.csv', num_rows=10000):
    df = pd.read_csv(file_path, nrows=num_rows)
    return df['temizlenmis_metin'].tolist()

# Anahtar kelimeleri okuma
def get_keywords(file_path='keywords.csv',num_keywords=100000,fill_value='geçersiz'):
    df = pd.read_csv(file_path)
    # NaN değerlerini boş stringlerle doldurma
    

    
    keyword_columns = ['Keyword_1','Keyword_2','Keyword_3','Keyword_4','Keyword_5']
    score_columns = ['Score_1,Score_2,Score_3,Score_4','Score_5']

    
    # NaN değerlerinin hangi sütunlarda olduğunu tespit etme
    nan_columns = df[keyword_columns].isna().any()

    # Hangi sütunlarda NaN değerler olduğunu yazdırma
    for col, has_nan in nan_columns.items():
        if has_nan:
            print(f"{col} sütununda NaN değerler var.")

    # NaN değerlerini belirli bir değerle doldurma (örneğin, boş string)
    df[keyword_columns] = df[keyword_columns].fillna(fill_value)
    df[score_columns]=df[score_columns].fillna(fill_value)
    
    keywords = df[keyword_columns].values.flatten().tolist()  # Anahtar kelimeleri tek bir listeye dönüştürün
    score= df[score_columns].values.flatten().tolist() 
    #keywords = [kw for kw in keywords if pd.notna(kw)]  # NaN olmayan değerleri alın
    # Anahtar kelimelerin sayısını belirli bir limite göre sınırlayın
    keywords = keywords[:num_keywords]

    return keywords

texts = get_text(num_rows=10000)

# texts listesindeki np.nan değerlerini boş string ile değiştirme
texts = [text if isinstance(text, str) else "" for text in texts]
print(f"Toplam metin sayısı: {len(texts)}")


keywords = get_keywords(num_keywords=100000)
print(f"Toplam anahtar kelime sayısı: {len(keywords)}")

score = get_keywords(num_keywords=100000)
print(f"Toplam anahtar kelime sayısı: {len(keywords)}")

# TF-IDF vektörleştiricisini oluşturma ve metinler ile anahtar kelimeleri encode etme
tfidf_vectorizer = TfidfVectorizer()
text_tfidf = tfidf_vectorizer.fit_transform(texts)
keyword_tfidf = tfidf_vectorizer.transform(keywords)

# Benzerlik hesaplama
similarity_matrix = cosine_similarity(text_tfidf, keyword_tfidf)



# Her metin için en yüksek benzerlik oranına sahip anahtar kelimeleri bulma
top_n =5  # İlk 5 anahtar kelimeyi alacağız
top_keywords_per_document = []

for idx, row in enumerate(similarity_matrix):
    sorted_indices = row.argsort()[::-1]  # Benzerlik oranına göre büyükten küçüğe sıralama
    text_tfidf_array = text_vector.toarray().flatten()
    top_keywords = []
    top_scores = []
    scores_for_text = (text_tfidf_array @ scores.T).flatten()
    # En yüksek skorlara sahip anahtar kelimeleri seçme
    sorted_indices = scores_for_text.argsort()[::-1]
    used_keywords=set()

    for i in sorted_indices:
        if len(top_keywords) >= top_n:
            break
        # Her bir skor için en yüksek 5 anahtar kelimeyi seçin
        top_scores_for_keyword = scores[i]
        top_indices_for_keyword = top_scores_for_keyword.argsort()[::-1]
        for j in top_indices_for_keyword:
            keyword = keywords[i, j]
            score = top_scores_for_keyword[j]
            if len(top_keywords) >= top_n:
                break
            top_keywords.append(keyword)
            top_scores.append(score)

    top_keywords_per_document.append((idx + 1, list(zip(top_keywords, top_scores))))


# Sonuçları yazdırma
for doc_id, keywords_scores in top_keywords_per_document:
    print(f"Metin {doc_id}:")
    for keyword, score in keywords_scores:
        print(f"Keyword: {keyword}, Similarity: {score:.4f}")
    print("\n")


Toplam metin sayısı: 10000
Keyword_6 sütununda NaN değerler var.
Keyword_9 sütununda NaN değerler var.
Toplam anahtar kelime sayısı: 100000


NameError: name 'text_vector' is not defined

In [12]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

def clean_text(text):
    return '' if pd.isna(text) else text

# CSV dosyasından belirli sayıda metin okuma
def get_text(file_path='temizlenmis_metin.csv', num_rows=10000):
    df = pd.read_csv(file_path, nrows=num_rows)
    return df['temizlenmis_metin'].tolist()

# Anahtar kelimeleri ve skorları okuma
def get_keywords_and_scores(file_path='keywords.csv', num_keywords=5000, fill_value='geçersiz'):
    df = pd.read_csv(file_path)
    keyword_columns = ['Keyword_1', 'Keyword_2', 'Keyword_3', 'Keyword_4', 'Keyword_5']
    score_columns = ['Score_1', 'Score_2', 'Score_3', 'Score_4', 'Score_5']

    # NaN değerlerini doldurma
    df[keyword_columns] = df[keyword_columns].fillna(fill_value)
    df[score_columns] = df[score_columns].fillna(0)

    # Anahtar kelimeler ve skorları alma
    keywords = df[keyword_columns].values.flatten().tolist()[:num_keywords]
    scores = df[score_columns].values.flatten().tolist()[:num_keywords]

    return keywords, scores

texts = get_text(num_rows=10000)

# texts listesindeki NaN değerlerini temizleme
texts = [clean_text(text) for text in texts]
print(f"Toplam metin sayısı: {len(texts)}")

keywords, scores = get_keywords_and_scores(num_keywords=50000)
print(f"Toplam anahtar kelime sayısı: {len(keywords)}")

# TF-IDF vektörleştiricisini oluşturma ve metinler ile anahtar kelimeleri encode etme
tfidf_vectorizer = TfidfVectorizer()
text_tfidf = tfidf_vectorizer.fit_transform(texts)
keyword_tfidf = tfidf_vectorizer.transform(keywords)

# Benzerlik hesaplama
similarity_matrix = cosine_similarity(text_tfidf, keyword_tfidf)

# Her metin için en yüksek benzerlik oranına sahip 5 farklı anahtar kelimeyi bulma
top_n = 5  # İlk 5 anahtar kelimeyi alacağız
top_keywords_per_document = []

for idx, row in enumerate(similarity_matrix):
    sorted_indices = row.argsort()[::-1]  # Benzerlik oranına göre büyükten küçüğe sıralama
    selected_keywords = set()  # Farklı anahtar kelimeleri takip etmek için set kullanıyoruz
    top_keywords = []
    
    for i in sorted_indices:
        keyword = keywords[i]
        score = row[i]
        
        if keyword not in selected_keywords and len(top_keywords) < top_n:
            top_keywords.append((keyword, score))
            selected_keywords.add(keyword)
        
        if len(top_keywords) >= top_n:
            break

    top_keywords_per_document.append({
        "title": f"Metin {idx + 1}",  # Eğer başlıklar varsa, buraya başlıkları ekleyin
        "text": texts[idx],
        "keywords": top_keywords
    })

# Sonuçları DataFrame'e dönüştürme ve CSV'ye yazma
results_df = pd.DataFrame(top_keywords_per_document)
results_df.to_csv('top_keywords_per_document.csv', index=False)

"""# Sonuçları yazdırma
for doc_id, keywords_scores in top_keywords_per_document:
    print(f"Metin {doc_id}:")
    for keyword, score in keywords_scores:
        print(f"Keyword: {keyword}, Similarity: {score:.4f}")
    print("\n")"""



Toplam metin sayısı: 10000
Toplam anahtar kelime sayısı: 50000


'# Sonuçları yazdırma\nfor doc_id, keywords_scores in top_keywords_per_document:\n    print(f"Metin {doc_id}:")\n    for keyword, score in keywords_scores:\n        print(f"Keyword: {keyword}, Similarity: {score:.4f}")\n    print("\n")'

In [15]:
import pandas as pd
from pymongo import MongoClient

# MongoDB bağlantısı
client = MongoClient('mongodb://localhost:27017/')  # MongoDB sunucunuza bağlanın
db = client['EgitimDatabase']  # Kullanmak istediğiniz veritabanı adı
collection = db['test']  # Güncellemek istediğiniz koleksiyon adı

# MongoDB'den metinleri alma
mongo_texts = collection.find({}, {'title': 1, 'text': 1, '_id': 0})
mongo_texts_dict = {doc['title']: doc['text'] for doc in mongo_texts}

# CSV dosyasını okuma
results_df = pd.read_csv('top_keywords_per_document.csv')

# Başlıkları ve metinleri eşleştirme
# Başlıkları eşleştirme
title_mapping = {f"Metin {i+1}": title for i, title in enumerate(mongo_texts_dict.keys())}

# Metinleri eşleştirme
text_mapping = {title: mongo_texts_dict[title] for title in title_mapping.values()}

# Başlıkları ve metinleri CSV'ye ekleme
results_df['title'] = results_df['title'].map(title_mapping).fillna(results_df['title'])
results_df['text'] = results_df['text'].map(text_mapping).fillna(results_df['text'])

# Güncellenmiş CSV dosyasını kaydetme
results_df.to_csv('top_keywords_per_document_updated.csv', index=False)


In [24]:
import pandas as pd
from transformers import AutoModel, AutoTokenizer,pipeline
import torch
from sklearn.metrics.pairwise import cosine_similarity
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")

classifier = pipeline('zero-shot-classification', model='MoritzLaurer/mDeBERTa-v3-base-mnli-xnli')

# Load model directly
from transformers import AutoTokenizer, AutoModelForSequenceClassification

tokenizer = AutoTokenizer.from_pretrained("MoritzLaurer/mDeBERTa-v3-base-mnli-xnli")
model = AutoModelForSequenceClassification.from_pretrained("MoritzLaurer/mDeBERTa-v3-base-mnli-xnli")

sequence_to_classify = "Angela Merkel ist eine Politikerin in Deutschland und Vorsitzende der CDU"
candidate_labels = ["politics", "economy", "entertainment", "environment"]
output = classifier(sequence_to_classify, candidate_labels, multi_label=False)
print(output)



c:\gitProjects\yeni\.venv\lib\site-packages\huggingface_hub\file_download.py:1150: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
c:\gitProjects\yeni\.venv\lib\site-packages\transformers\utils\generic.py:309: FutureWarning: `torch.utils._pytree._register_pytree_node` is deprecated. Please use `torch.utils._pytree.register_pytree_node` instead.
  _torch_pytree._register_pytree_node(


{'sequence': 'Angela Merkel ist eine Politikerin in Deutschland und Vorsitzende der CDU', 'labels': ['politics', 'economy', 'environment', 'entertainment'], 'scores': [0.9658799767494202, 0.022846756502985954, 0.0073339128866791725, 0.003939332906156778]}


In [25]:
from transformers import GPT2Tokenizer, GPT2LMHeadModel

# Model ve tokenizer'ı yükleme
tokenizer = GPT2Tokenizer.from_pretrained("gpt2")
model = GPT2LMHeadModel.from_pretrained("gpt2")

def generate_subheadings(title, keywords):
    input_text = f"Başlık: {title}\nAnahtar kelimeler: {', '.join(keywords)}\nAlt Başlıklar:"
    inputs = tokenizer.encode(input_text, return_tensors='pt')
    outputs = model.generate(inputs, max_length=50, num_return_sequences=1, temperature=0.7)
    generated_text = tokenizer.decode(outputs[0], skip_special_tokens=True)
    return generated_text

# Örnek kullanım
title = "Angela Merkel"
keywords = ["politics", "CDU", "Germany"]
print(generate_subheadings(title, keywords))


tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

c:\gitProjects\yeni\.venv\lib\site-packages\huggingface_hub\file_download.py:159: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\info\.cache\huggingface\hub\models--gpt2. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to see activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)


vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

c:\gitProjects\yeni\.venv\lib\site-packages\transformers\generation\configuration_utils.py:389: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.7` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Başlık: Angela Merkel
Anahtar kelimeler: politics, CDU, Germany
Alt Başlıklar: politics, CDU, Germany
Anahtar kelimeler: politics, CD


Gpt Modelini Yükleme 

In [30]:
from transformers import GPT2LMHeadModel, GPT2Tokenizer, Trainer, TrainingArguments
import pandas as pd 
import torch
from torch.utils.data import Dataset, DataLoader

# Tokenizer ve model yükleme
model_name = 'gpt2'
model = GPT2LMHeadModel.from_pretrained(model_name)
tokenizer = GPT2Tokenizer.from_pretrained(model_name)

# Eğitim verisini yükleme
df = pd.read_csv("top_keywords_per_document_updated.csv")

# Custom Dataset sınıfı
class CustomDataset(Dataset):
    def __init__(self, dataframe):
        self.dataframe = dataframe
        self.texts = dataframe['text'].tolist()

    def __len__(self):
        return len(self.dataframe)

    def __getitem__(self, idx):
        text = self.texts[idx]
        tokenized = tokenizer(text, padding='max_length', truncation=True, max_length=512, return_tensors="pt")
        return {'input_ids': tokenized['input_ids'].squeeze(), 'attention_mask': tokenized['attention_mask'].squeeze()}

# Dataset ve DataLoader oluşturma
dataset = CustomDataset(df)
dataloader = DataLoader(dataset, batch_size=4, shuffle=True)

# Eğitim parametreleri
training_args = TrainingArguments(
    output_dir='./results',  # Çıktı dizini belirtin
    per_device_train_batch_size=4,
    per_device_eval_batch_size=4,
    num_train_epochs=3,
    logging_dir='./logs',
)

# Trainer'ı oluşturun ve eğitimi başlatın
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=dataset,
)

trainer.train()

def generate_custom_subheadings(title, keywords, model, tokenizer, num_subheadings=5):
    prompt = f"Başlık: {title}\nAnahtar Kelimeler: {', '.join(keywords)}\nLütfen başlık ve anahtar kelimelerle uyumlu olan ve en az üç anahtar kelimeyi içeren, başlıkla benzer bir kelime içeren {num_subheadings} alt başlık önerisi oluşturun."

    inputs = tokenizer(prompt, return_tensors='pt')
    outputs = model.generate(inputs['input_ids'], max_length=50, num_return_sequences=num_subheadings, no_repeat_ngram_size=2, early_stopping=True)
    subheadings = [tokenizer.decode(output, skip_special_tokens=True) for output in outputs]
    return subheadings

# Test etme
title = "Örnek Başlık"  # Başlık için örnek değer
keywords = ["anahtar1", "anahtar2", "anahtar3"]  # Anahtar kelimeler için örnek değer
subheadings = generate_custom_subheadings(title, keywords, model, tokenizer)
for i, subheading in enumerate(subheadings):
    print(f"Subheading {i+1}: {subheading}")


c:\gitProjects\yeni\.venv\lib\site-packages\huggingface_hub\file_download.py:1150: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


ImportError: Using the `Trainer` with `PyTorch` requires `accelerate>=0.20.1`: Please run `pip install transformers[torch]` or `pip install accelerate -U`

In [ ]:
def get_embeddings(text):
    inputs = tokenizer(text, return_tensors='pt', truncation=True, padding=True)
    with torch.no_grad():
        outputs = model(**inputs)
    # İlk özniteliklerin ortalamasını alarak vektör elde etme
    embeddings = outputs.last_hidden_state.mean(dim=1).squeeze()
    return embeddings

def generate_subheadings(title, keywords, top_n=5):
    title_embedding = get_embeddings(title)
    keyword_embeddings = [get_embeddings(keyword) for keyword in keywords]

    similarities = [cosine_similarity(title_embedding.unsqueeze(0), keyword_embedding.unsqueeze(0))[0][0] for keyword_embedding in keyword_embeddings]
    sorted_indices = sorted(range(len(similarities)), key=lambda i: similarities[i], reverse=True)

    # Benzerliklere göre anahtar kelimelerden alt başlıklar oluşturma
    subheadings = [keywords[i] for i in sorted_indices[:top_n]]
    return subheadings

# Örnek veri
title = "Veri Bilimi Nedir?"
keywords = ["Makine Öğrenmesi", "Büyük Veri", "Yapay Zeka", "1936", "Veri Madenciliği", "Derin Öğrenme", "Doğal Dil İşleme", "1982", "Yapay Sinir Ağları", "Kümeleme"]

# Alt başlıkları oluşturma
subheadings = generate_subheadings(title, keywords)
print("Alt Başlıklar:")
for subheading in subheadings:
    print(f"- {subheading}")


In [21]:
import pandas as pd
from transformers import AutoModel, AutoTokenizer
import torch
from sklearn.metrics.pairwise import cosine_similarity

# Model ve tokenizer'ı yükleme
model_name = 'dbmdz/distilbert-base-turkish-cased'
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModel.from_pretrained(model_name)

def get_embeddings(text, max_length=512):
    """
    Metni gömme (embedding) vektörüne dönüştürür.
    """
    inputs = tokenizer(text, return_tensors='pt', truncation=True, padding=True, max_length=max_length)
    with torch.no_grad():
        outputs = model(**inputs)
    # İlk özniteliklerin ortalamasını alarak vektör elde etme
    embeddings = outputs.last_hidden_state.mean(dim=1).squeeze()
    return embeddings

def generate_subheadings(title, keywords, top_n=5):
    """
    Başlık ve anahtar kelimeleri kullanarak alt başlıklar oluşturur.
    """
    title_embedding = get_embeddings(title)
    keyword_embeddings = [get_embeddings(keyword) for keyword in keywords]

    # Başlık ile anahtar kelimeler arasındaki benzerlikleri hesaplama
    similarities = [cosine_similarity(title_embedding.unsqueeze(0), keyword_embedding.unsqueeze(0))[0][0].item() for keyword_embedding in keyword_embeddings]
    sorted_indices = sorted(range(len(similarities)), key=lambda i: similarities[i], reverse=True)

    # Benzerliklere göre anahtar kelimelerden alt başlıklar oluşturma
    subheadings = [keywords[i] for i in sorted_indices[:top_n]]
    return subheadings

# CSV dosyasını okuma
df = pd.read_csv('top_keywords_per_document.csv')

# Başlıkları ve anahtar kelimeleri içeren sütun isimlerini belirleyin
title_column = 'title'  # Başlıkları içeren sütun
keywords_column = 'keywords'  # Anahtar kelimeleri içeren sütun

# Başlık ve anahtar kelimeleri içeren verileri çekme
titles = df[title_column].dropna().tolist()
keywords_list = df[keywords_column].dropna().tolist()

# Anahtar kelimeleri virgülle ayırarak listeye dönüştürme
keywords_list = [keywords.split(',') for keywords in keywords_list]

# Başlık ve anahtar kelimeleri kullanarak alt başlıkları oluşturma
for title, keywords in zip(titles, keywords_list):
    subheadings = generate_subheadings(title, keywords)
    print(f"Başlık: {title}")
    print("Alt Başlıklar:")
    for subheading in subheadings:
        print(f"- {subheading}")
    print("\n")


c:\gitProjects\yeni\.venv\lib\site-packages\transformers\utils\generic.py:441: FutureWarning: `torch.utils._pytree._register_pytree_node` is deprecated. Please use `torch.utils._pytree.register_pytree_node` instead.
  _torch_pytree._register_pytree_node(
c:\gitProjects\yeni\.venv\lib\site-packages\huggingface_hub\file_download.py:1150: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
c:\gitProjects\yeni\.venv\lib\site-packages\transformers\utils\generic.py:309: FutureWarning: `torch.utils._pytree._register_pytree_node` is deprecated. Please use `torch.utils._pytree.register_pytree_node` instead.
  _torch_pytree._register_pytree_node(
c:\gitProjects\yeni\.venv\lib\site-packages\transformers\utils\generic.py:309: FutureWarning: `torch.utils._pytree._register_pytree_node` is deprecated. Please use `torch.utils._pytree.register_pytree_n

pytorch_model.bin:   0%|          | 0.00/273M [00:00<?, ?B/s]

c:\gitProjects\yeni\.venv\lib\site-packages\huggingface_hub\file_download.py:159: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\info\.cache\huggingface\hub\models--dbmdz--distilbert-base-turkish-cased. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to see activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)
c:\gitProjects\yeni\.venv\lib\site-packages\transformers\modeling_utils.py:519: FutureWarning: You are u

Başlık: Metin 1
Alt Başlıklar:
-  ('kapital'
-  ('engelsin'
- [('marxın'
-  ('hegelin'
-  ('jenny'


Başlık: Metin 2
Alt Başlıklar:
-  ('pir'
-  ('dostlar'
- [('ruhi'
-  ('sunun'
-  ('sıdıka'


Başlık: Metin 3
Alt Başlıklar:
- [('bilgisayarlar'
-  ('destekli'
-  ('bilgisayarı'
-  ('dişli'
-  ('bilgisayarlı'


Başlık: Metin 4
Alt Başlıklar:
-  ('drama'
- [('edebiyatın'
-  ('edebî'
-  ('edeb'
-  ('arapçadaki'


Başlık: Metin 5
Alt Başlıklar:
-  ('malzemelerin'
- [('mühendisliği'
-  ('dalıdır'
-  ('ilgilenir'
-  ('mekatronik'


Başlık: Metin 6
Alt Başlıklar:
- [('esperanto'
-  ('bahâî'
-  ('zamenhof'
-  ('esperantonun'
-  ('zamenhofun'


Başlık: Metin 7
Alt Başlıklar:
-  ('yürüme'
-  ('robotun'
- [('qrio'
-  ('sony'
-  ('qrionun'


Başlık: Metin 8
Alt Başlıklar:
-  ('yen'
- [('sutopu'
-  ('binicilik'
-  ('kalamış'
-  ('galatasarayın'


Başlık: Metin 9
Alt Başlıklar:
-  ('gübre'
- [('tarımda'
-  ('verimi'
-  ('tarımdaki'
-  ('yetiştiriciliği'


Başlık: Metin 10
Alt Başlıklar:
- [('jeoloji'

KeyboardInterrupt: 

In [22]:
import pandas as pd
from transformers import AutoModel, AutoTokenizer
import torch
from sklearn.metrics.pairwise import cosine_similarity
from itertools import combinations

# Model ve tokenizer'ı yükleme
model_name = 'dbmdz/distilbert-base-turkish-cased'
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModel.from_pretrained(model_name)

def get_embeddings(text, max_length=512):
    """
    Metni gömme (embedding) vektörüne dönüştürür.
    """
    inputs = tokenizer(text, return_tensors='pt', truncation=True, padding=True, max_length=max_length)
    with torch.no_grad():
        outputs = model(**inputs)
    embeddings = outputs.last_hidden_state.mean(dim=1).squeeze()
    return embeddings

def generate_subheadings(title, keywords, top_n=5):
    """
    Başlık ve anahtar kelimeleri kullanarak alt başlıklar oluşturur.
    """
    title_embedding = get_embeddings(title)
    
    # Anahtar kelimelerden ikili ve üçlü kombinasyonlar oluşturma
    keyword_combinations = []
    for i in range(2, 4):  # 2 ve 3 kelimelik kombinasyonlar
        keyword_combinations.extend([' '.join(comb) for comb in combinations(keywords, i)])
    
    # Kombinasyonlar için gömme vektörleri oluşturma
    combination_embeddings = [get_embeddings(comb) for comb in keyword_combinations]

    # Başlık ile kombinasyonlar arasındaki benzerlikleri hesaplama
    similarities = [cosine_similarity(title_embedding.unsqueeze(0), comb_embedding.unsqueeze(0))[0][0].item() for comb_embedding in combination_embeddings]
    
    # Benzerliklere göre en yüksek 5 kombinasyonu seçme
    top_indices = sorted(range(len(similarities)), key=lambda i: similarities[i], reverse=True)[:top_n]
    subheadings = [keyword_combinations[i] for i in top_indices]
    
    return subheadings

# CSV dosyasını okuma
df = pd.read_csv('top_keywords_per_document.csv')

# Başlıkları ve anahtar kelimeleri içeren sütun isimlerini belirleyin
title_column = 'title'  # Başlıkları içeren sütun
keywords_column = 'keywords'  # Anahtar kelimeleri içeren sütun

# Başlık ve anahtar kelimeleri içeren verileri çekme
titles = df[title_column].dropna().tolist()
keywords_list = df[keywords_column].dropna().tolist()

# Anahtar kelimeleri virgülle ayırarak listeye dönüştürme
keywords_list = [keywords.split(',') for keywords in keywords_list]

# Başlık ve anahtar kelimeleri kullanarak alt başlıkları oluşturma
for title, keywords in zip(titles, keywords_list):
    subheadings = generate_subheadings(title, keywords)
    print(f"Başlık: {title}")
    print("Alt Başlıklar:")
    for subheading in subheadings:
        print(f"- {subheading}")
    print("\n")


c:\gitProjects\yeni\.venv\lib\site-packages\huggingface_hub\file_download.py:1150: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
c:\gitProjects\yeni\.venv\lib\site-packages\transformers\modeling_utils.py:519: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.

Başlık: Metin 1
Alt Başlıklar:
-  ('engelsin'  ('kapital'
- [('marxın'  ('kapital'
- [('marxın'  ('engelsin'
-  ('hegelin'  ('kapital'
- [('marxın'  ('hegelin'


Başlık: Metin 2
Alt Başlıklar:
-  ('dostlar'  ('pir'
- [('ruhi'  ('dostlar'
- [('ruhi'  ('pir'
-  ('pir'  ('sıdıka'
-  ('sunun'  ('pir'


Başlık: Metin 3
Alt Başlıklar:
- [('bilgisayarlar'  ('bilgisayarı'
- [('bilgisayarlar'  ('destekli'
- [('bilgisayarlar'  ('dişli'
- [('bilgisayarlar'  ('bilgisayarlı'
-  ('destekli'  ('dişli'


Başlık: Metin 4
Alt Başlıklar:
- [('edebiyatın'  ('drama'
-  ('edebî'  ('drama'
- [('edebiyatın'  ('edebî'
- [('edebiyatın'  ('edeb'
-  ('edeb'  ('drama'


Başlık: Metin 5
Alt Başlıklar:
- [('mühendisliği'  ('malzemelerin'
- [('mühendisliği'  ('mekatronik'
- [('mühendisliği'  ('dalıdır'
- [('mühendisliği'  ('ilgilenir'
-  ('mekatronik'  ('malzemelerin'




KeyboardInterrupt: 

In [17]:
from gensim import corpora
from gensim.models import LdaMulticore
import pandas as pd

# CSV dosyasını okuma
df = pd.read_csv('temizlenmis_metin.csv')

# Verinin bir alt kümesini seçme
df_sample = df.sample(n=10000, random_state=100)

# NaN veya float olan değerleri boş string ile dolduruyoruz
df_sample['temizlenmis_metin'] = df_sample['temizlenmis_metin'].fillna('')
# Kelimeleri token'lara ayırma
tokenized_text = [text.split() for text in df_sample['temizlenmis_metin']]

# Dictionary ve Corpus oluşturma
id2word = corpora.Dictionary(tokenized_text)
corpus = [id2word.doc2bow(text) for text in tokenized_text]

# LDA Modelini Eğitme
lda_model = LdaMulticore(
    corpus=corpus,
    id2word=id2word,
    num_topics=5,
    random_state=100,
    chunksize=50,
    passes=5,
    alpha='symmetric',
    eta='auto',
    per_word_topics=True,
    workers=4  # Paralel iş parçacıkları kullanarak performansı artırır
)

# Sonuçları görüntüleme
for idx, topic in lda_model.print_topics(-1):
    print(f"Topic: {idx}\nWords: {topic}\n")

# Alt kümesini kaydetme
df_sample.to_csv('alt_küme.csv', index=False)


Topic: 0
Words: 0.032*"futbolcuları" + 0.027*"aligncenter" + 0.021*"colspan" + 0.021*"alignleft" + 0.011*"millî" + 0.010*"width" + 0.008*"stylebackgroundcoloreee" + 0.006*"doğumlular" + 0.005*"fc" + 0.005*"gurbetçi"

Topic: 1
Words: 0.003*"doğumlular" + 0.002*"dizileri" + 0.002*"albümleri" + 0.002*"styletextaligncenter" + 0.001*"civil" + 0.001*"i" + 0.001*"çıkışlı" + 0.001*"stüdyo" + 0.001*"lerde" + 0.001*"gitar"

Topic: 2
Words: 0.002*"b" + 0.002*"türüdür" + 0.002*"c" + 0.001*"cinsine" + 0.001*"m" + 0.001*"ios" + 0.001*"ilçenin" + 0.001*"sirius" + 0.001*"getty" + 0.001*"f"

Topic: 3
Words: 0.004*"doğumlular" + 0.003*"ilinin" + 0.003*"ölenler" + 0.003*"ii" + 0.002*"tarihçe" + 0.002*"i" + 0.002*"ö" + 0.002*"uzaklıktadır" + 0.002*"ili" + 0.002*"mahalleleri"

Topic: 4
Words: 0.004*"eurovision" + 0.003*"ngc" + 0.002*"tour" + 0.002*"takımyıldızı" + 0.002*"taarruzu" + 0.002*"etap" + 0.002*"galaksidir" + 0.002*"kg" + 0.002*"yarışmasında" + 0.002*"astronom"



In [27]:
from sklearn.feature_extraction.text import TfidfVectorizer
import pandas as pd
import numpy as np
from scipy.sparse import csr_matrix

# Metinleri okuma
df_sample = pd.read_csv('temizlenmis_metin.csv')
df_sample = df.sample(n=10000, random_state=100)
df_sample['temizlenmis_metin'] = df_sample['temizlenmis_metin'].fillna('')

# TF-IDF Vektörizer'i tanımlama ve uygulama
vectorizer = TfidfVectorizer()
X = vectorizer.fit_transform(df_sample['temizlenmis_metin'])
feature_names = vectorizer.get_feature_names_out()

# En yüksek TF-IDF değerlerini bulma
def get_top_keywords_sparse(sparse_matrix, feature_names, top_n):
    # Sadece her satır için en yüksek TF-IDF değerlerini bulma
    top_keywords = {}
    for i in range(sparse_matrix.shape[0]):
        row = sparse_matrix[i, :]
        top_indices = np.argsort(row.data)[-top_n:]  # En yüksek `top_n` TF-IDF değerlerinin indeksleri
        top_features = {feature_names[idx]: row.data[idx] for idx in top_indices}
        top_keywords[i] = top_features
    return top_keywords

# En yüksek TF-IDF değerlerini ve anahtar kelimeleri bulma
top_n = 10
top_keywords = get_top_keywords_sparse(X, feature_names, top_n)

# Sonuçları DataFrame'e dönüştürme
df_top_keywords = pd.DataFrame.from_dict(top_keywords, orient='index').fillna(0)

# Sonuçları CSV dosyasına kaydetme
df_top_keywords.to_csv('top_keywords_per_text_sparse.csv', index=False)

print("Her metin için en yüksek 10 TF-IDF değerini içeren CSV dosyası oluşturuldu.")


Her metin için en yüksek 10 TF-IDF değerini içeren CSV dosyası oluşturuldu.


In [31]:
from sklearn.feature_extraction.text import TfidfVectorizer
import pandas as pd
import numpy as np

# Metinleri okuma
df_sample = pd.read_csv('temizlenmis_metin.csv')
df_sample = df.sample(n=10000, random_state=100)
df_sample['temizlenmis_metin'] = df_sample['temizlenmis_metin'].fillna('')

# TF-IDF Vektörizer'i tanımlama ve uygulama
vectorizer = TfidfVectorizer(max_df=0.8, min_df=2, ngram_range=(1, 2))
X = vectorizer.fit_transform(df_sample['temizlenmis_metin'])
feature_names = vectorizer.get_feature_names_out()

# En yüksek TF-IDF değerlerini ve kelimeleri bulma
def get_top_keywords_sparse(sparse_matrix, feature_names, top_n):
    top_keywords = {}
    for i in range(sparse_matrix.shape[0]):
        row = sparse_matrix[i, :]
        # TF-IDF değerlerini ve kelimeleri bulma
        top_indices = np.argsort(row.data)[-top_n:]  # En yüksek `top_n` TF-IDF değerlerinin indeksleri
        top_features = {feature_names[idx]: row.data[idx] for idx in top_indices}
        top_keywords[i] = top_features
    return top_keywords

# Her metin için en yüksek TF-IDF değerlerini ve anahtar kelimeleri bulma
top_n = 10
top_keywords = get_top_keywords_sparse(X, feature_names, top_n)

# Sonuçları DataFrame'e dönüştürme
def convert_to_dataframe(top_keywords):
    rows = []
    for idx, keywords in top_keywords.items():
        for word, score in keywords.items():
            rows.append({'Document Index': idx, 'Keyword': word, 'TF-IDF Score': score})
    return pd.DataFrame(rows)

df_top_keywords = convert_to_dataframe(top_keywords)

# Sonuçları CSV dosyasına kaydetme
df_top_keywords.to_csv('top_keywords_per_text_detailed2.csv', index=False)

print("Her metin için en yüksek TF-IDF değerlerini ve kelimeleri içeren CSV dosyası oluşturuldu.")


Her metin için en yüksek TF-IDF değerlerini ve kelimeleri içeren CSV dosyası oluşturuldu.


In [2]:
import re
import pandas as pd
import nltk
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer

# NLTK stopwords'ü indir
nltk.download('stopwords')
# Stopwords dosyasını okuma ve liste haline getirme
def load_stop_words(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        stop_words = {line.strip().lower() for line in file}
    return stop_words

# Örneğin 'stopwords.txt' dosyasını kullanarak stopwords'leri yükleyin
custom_stop_words = load_stop_words('gereksiz_kelimeler.txt')



# Genel ve özel stopwords listesini birleştirme
general_stop_words = set(stopwords.words('turkish'))
custom_stop_words = load_stop_words('gereksiz_kelimeler.txt')
all_stop_words = general_stop_words.union(custom_stop_words)

# CSV dosyasını yükleme
df = pd.read_csv('texts_egitim.csv')

# 'metinler' sütununu çekme
metinler = df['metinler'].tolist()[:10000]

# Metin temizleme fonksiyonu
def clean_text(text):
    # Metni küçük harfe çevirme
    text = text.lower()
    # Noktalama işaretlerini ve sayıları temizleme
    text = re.sub(r'\d+', '', text)  # Sayıları çıkar
    text = re.sub(r'[^\w\s]', '', text)  # Noktalama işaretlerini çıkar
    # Gereksiz karakterleri çıkar
    text = re.sub(r'__|\|', '', text)  # __ ve | karakterlerini çıkar
    # Gereksiz kelimeleri çıkarma
    words = text.split()
    filtered_words = [word for word in words if word not in all_stop_words]
    
    cleaned_text = ' '.join(filtered_words)
    
    # Eğer temizlenmiş metin boşsa, boş string döndür
    if not cleaned_text:
        return ''
    
    return cleaned_text

# Metinleri temizleme işlemi
df['temizlenmis_metin'] = df['metinler'].apply(clean_text)

# TF-IDF hesaplaması
vectorizer = TfidfVectorizer(max_features=10)  # En fazla 10 anahtar kelime
X = vectorizer.fit_transform(df['temizlenmis_metin'])

# Anahtar kelimeleri çıkarma
df['keywords'] = vectorizer.inverse_transform(X)

# Temizlenmiş metinleri ve anahtar kelimeleri CSV dosyasına kaydetme
df[['temizlenmis_metin', 'keywords']].to_csv('temizlenmis_metin_keywords.csv', index=False)

# Çıkarılan anahtar kelimeleri ekrana yazdırma
print("Metinlerden çıkarılan anahtar kelimeler:")
for keywords in df['keywords']:
    print(", ".join(keywords))


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\info\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Metinlerden çıkarılan anahtar kelimeler:
ii, millî, doğumlular, ölenler
doğumlular, ölenler
ii


ii, millî

ii, millî
ii
millî


ii, millî, doğumlular, ölenler

doğumlular, ölenler





doğumlular

ii, millî
millî, doğumlular, ölenler
doğumlular


doğumlular
millî
ii, millî



doğumlular

ii, millî, futbolcuları
millî, doğumlular


ii

doğumlular



doğumlular, ölenler
millî
ii, millî
ii, millî



millî, colspan
doğumlular, ölenler
ii, millî

ii



millî





ii, doğumlular
millî


doğumlular, ölenler

ii, millî



doğumlular, ölenler
doğumlular, ölenler

ii
millî
ii, millî
ii, millî
millî
ii, millî
ii
ii, millî
ii, millî
ii
ii, millî
ii, millî
ii, millî
ii
millî
ii, millî
millî
doğumlular
doğumlular, ölenler

ii, millî
ii, millî
ii, millî
ii, millî
ii, millî
millî
ii
ii


millî
millî

millî
ii

ii, millî

ii
millî
ii
ii



millî



ii



ii
ii


ii
ii
ii
ii
ii



ii

ii

ii









ii


ii
ii



ii

ii
ii



ii
ii


ii









ii






millî
ii, millî
ii, millî
ii, millî
ii, millî
i

In [8]:
import re
import pandas as pd
import spacy
from sklearn.feature_extraction.text import TfidfVectorizer

# Using spacy.load().
import spacy
nlp = spacy.load("tr_core_news_md")

# Importing as module.
import tr_core_news_md
nlp = tr_core_news_md.load()

# Metin temizleme ve yüklemleri çıkarma fonksiyonu
def clean_and_remove_verbs(text):
    # Metni küçük harfe çevirme
    text = text.lower()
    
    # Noktalama işaretlerini, sayıları ve gereksiz karakterleri çıkarma
    text = re.sub(r'\d+', '', text)  # Sayıları çıkar
    text = re.sub(r'[^\w\s]', '', text)  # Noktalama işaretlerini çıkar
    text = re.sub(r'[^\w\s]|_', '', text)  # Ek gereksiz karakterleri çıkar
    
    # Metni tokenize etme ve yüklemleri çıkarma
    doc = nlp(text)
    
    # Yüklemleri çıkarma ve gereksiz kelimeleri temizleme
    cleaned_words = [token.text for token in doc if token.pos_ != 'VERB' and not token.is_stop]
    
    return ' '.join(cleaned_words)

# CSV dosyasını yükleyin
df = pd.read_csv('temizlenmis_metin.csv')

# Metinleri temizleyin ve yüklemleri çıkarın
df['temizlenmis_metin'] = df['temizlenmis_metin'].apply(clean_and_remove_verbs)

# TF-IDF hesaplama
vectorizer = TfidfVectorizer(max_features=10)  # En yüksek 10 özelliği seçeceğiz
tfidf_matrix = vectorizer.fit_transform(df['temizlenmis_metin'])

# En yüksek TF-IDF değerlerini alıp, kelimeleri belirleyin
feature_names = vectorizer.get_feature_names_out()
dense = tfidf_matrix.todense()
denselist = dense.tolist()

tfidf_df = pd.DataFrame(denselist, columns=feature_names)
top_keywords = tfidf_df.mean().sort_values(ascending=False).head(10)
print(top_keywords)

# Sonuçları CSV dosyasına kaydetme
top_keywords.to_csv('en_yuksek_tfidf_keywords.csv')


OSError: [E050] Can't find model 'tr_core_news_lg'. It doesn't seem to be a Python package or a valid path to a data directory.